In [1]:
import numpy as np
from scipy import sparse, linalg
import networkx as nx
from networkx.algorithms import bipartite
import multinetx as mx
import csv, os, sys
import matplotlib.pyplot as plt
from sklearn.preprocessing import normalize
from itertools import permutations

In [15]:
def create_layer_from_csv(file_path, node_start_id = 0): #TODO... TO WE NEED A FILTERING SET:, filtering_set = None):
    """
    Creates a network layer from a csv file
    
    The first column in the csv file should hold names of nodes to be interconnected between layers
    
    Attributes
    ----------
    file_path : str
        a name of a csv file to process
    node_start_id : int
        first id to assign to a node created
    filtering_set : set of ids (strings) 
        for filtering records to be used from the csv file
    """
    
    G = nx.Graph()
    
    #print('Number of keys in filtering set: {}'.format(len(filtering_set)))
    
    # first pass only creates the nodes with the appropriate bipartite attribute
    # bipartite = 0 is used for nodes to be interconnected between layers
    with open(file_path, encoding='utf8') as f:
        csv_reader = csv.reader(f)
        
        externally_connected = [] #what about duplicates, are they to be expected? yes so this is ok I think.
        internally_connected = set()
    
        for row in csv_reader:
            
            ext_node_str_id = row[0].strip()
        
            #if ext_node_str_id in filtering_set: #(not filtering_set) or #TODO activate no filtering if no filtering set is specified
            externally_connected.append(ext_node_str_id)
            internally_connected.add(row[1].strip())
            #else:
            #    print('Node not found in filtering set...')
            
    G.add_nodes_from(externally_connected, bipartite=0)
    G.add_nodes_from(internally_connected, bipartite=1)
    
    print('Added {} ext nodes to layer'.format(len(externally_connected)))
    print('Added {} int nodes to layer'.format(len(internally_connected)))
    
    # instead of forcing the bipatrite attribute like this we could possibly have done
    # nx.is_connected(G) -- but our layers are not connectd, right!
    # bottom_nodes, top_nodes = bipartite.sets(G)
    # possibly we could not be sure which set will be what A vs. B or B vs. A!
    
    # second pass creates a list of edges.
    # not sure which is better; reset the csv_reader or just create a new one, taking the latter option
    with open(file_path, encoding='utf8') as f:
        csv_reader = csv.reader(f)
        # get the data as list of tuples
        
        edges = [(row[0].strip(), row[1].strip()) for row in csv_reader] # TODO: filtering? if not filtering_set or row[0].strip() in filtering_set]
        
    G.add_edges_from(edges)
          
    print('Added {} edges to layer'.format(len(edges)), end='\n\n')
    
    # haven't still succeeded in triggering this exception, the way I'm assigning the bipartite attribude acc. to columns
    # in the csv, always creates a new node if trying that. 
    if not bipartite.is_bipartite(G):
        raise Exception('Network is not bipartite')
        
    # abandon labels for ids, here we are using the default value for the ordering parameter
    return nx.convert_node_labels_to_integers(G, first_label=node_start_id, ordering='default', label_attribute='name') #, externally_connected
    # we also have this function
    # nx.relabel_nodes(takes in the network and a dictionary)

In [16]:
def get_current_count_of_nodes(layers):
    """
    Returns the total count of nodes in list/collection/iterable! of networkX layers 
    
    """
    
    node_count = 0
    
    for layer in layers:
        node_count += layer.number_of_nodes()
        
    return node_count

In [17]:
def get_node_count_stats(graph):
    
    number_of_zero_bipatrite_nodes = len({n for n, d in graph.nodes(data=True) if d['bipartite']==0})
    number_of_one_bipartite_nodes = len({n for n, d in graph.nodes(data=True) if d['bipartite']==1})
    
    return graph.number_of_nodes(), number_of_zero_bipatrite_nodes, number_of_one_bipartite_nodes

In [18]:
def get_interconnect_nodes(layers):
    """
    Extracts the sets on nodes to be interconnected
    
    """
    
    sets = []
    
    for layer in layers:
        sets.append({n for n, d in layer.nodes(data=True) if d['bipartite']==0})
        
    return sets

In [19]:
def wire_interconnections(layers, interconnect_nodes):
    """
    Retruns a descriptive datastrcuture (a dict of lists) describing how the nodes are to be interconnected
    
    Attributes
    ----------
    layers : list
        list of networkX graphs
    interconnect_nodes : list
        contents of the list are sets of nodes to be interconnected in each layer
    
    """
    
    interconnect_nodes_by_name = {}
    
    for n,interconnect_set in enumerate(interconnect_nodes):
        for node_id in interconnect_set:
            
            name = layers[n].nodes[node_id]['name']
            
            if name not in interconnect_nodes_by_name:
                interconnect_nodes_by_name[name] = [node_id]
            else:
                interconnect_nodes_by_name[name].append(node_id)
            
    return interconnect_nodes_by_name

In [20]:
def persoal_matrix_from_defaulters(file_name, multilayernetwork):
    with open(file_name) as f:
        defaulters = f.readlines()
        
    defaulters = [x.strip() for x in defaulters]
    
    defaulter_indices = {}
    
    for defaulter in defaulters:
    
        for n, d in multilayernetwork.nodes(data=True):
            if d['name']==defaulter:
                
                if defaulter in defaulter_indices:
                    defaulter_indices[defaulter].append(n)
                else:
                    defaulter_indices[defaulter] = [n]
                    
    n = multilayernetwork.num_nodes
                    
    pers_matrix = sparse.lil_matrix((n, n))
    
    for indexes in defaulter_indices.values():
        
        # aren't there better ways to populate all indexes than gettin all 2 permutations of the doubled lists thrown into a set to remove duplications!
        for i,j in set(permutations(indexes + indexes, 2)):
            
            # in the docs they talk aboud slowness.... chack if problem
            pers_matrix[i,j] = 1
    
    return pers_matrix, defaulter_indices

In [21]:
# for the agri set we need to limit the 'loans_products' dataset to the ones present in the LL file, as the ones 
# relevant to the current timeframe

with open(os.path.join('.', 'll.csv'), encoding='utf8') as f:
    csv_reader = csv.reader(f)
    
    ll_dict = {row[0].strip(): (row[1].strip(), row[2].strip()) for row in csv_reader}
    #time_window = set(row[2] for row in csv_reader)
    #loan_ids = set(row[0] for row in csv_reader)

In [22]:
# for debugging...
with open(os.path.join('.', 'loans_products.csv'), encoding='utf8') as f:
    cr = csv.reader(f)
    
    x=set(row[1].strip() for row in cr)

In [23]:
# where are the csv files located, relative to the current folder where this script is run
directory = '.'

csv_files = ['loans_products.csv', 'areas.csv', 'districts.csv']

# each layer is a networkX network. Will be used to create a multilayer network
layers = []

#for f in os.listdir(directory):
for f in csv_files:
    
    # if other files than csv are present, skip those
    if f[-4:] != '.csv':
        continue
        
    file_path = os.path.join(directory, f)

    layers.append(create_layer_from_csv(file_path, get_current_count_of_nodes(layers))) #, ll_dict.keys()))
    
interconnect_nodes = get_interconnect_nodes(layers)
interconnections = wire_interconnections(layers, interconnect_nodes)

# there is a property multinetX::num_nodes() - but to use it here we would have to create the multilayer network first
# from the list of layers only..
N = get_current_count_of_nodes(layers) # not efficient but ok for now

print('Got total count of Nodes: {}'.format(N))

for l in layers:
    print('Nodes in layer: {}'.format(l.number_of_nodes()))

Added 62884 ext nodes to layer
Added 178 int nodes to layer
Added 62884 edges to layer

Added 79436 ext nodes to layer
Added 321 int nodes to layer
Added 79436 edges to layer

Added 79436 ext nodes to layer
Added 286 int nodes to layer
Added 79436 edges to layer

Got total count of Nodes: 159125
Nodes in layer: 52939
Nodes in layer: 53102
Nodes in layer: 53084


In [24]:
# adj_block = mx.lil_matrix(np.zeros((N, N))) #can't understend what lil has to do with multinetx here!
# couldn't we just as well do here:
# adj_block = sparse.lil_matrix(np.zeros((N, N))) # looks like being the same thing!
# for a square matrix of size 160K the memory needed for the above is 189 GiB!!!
adj_block = sparse.lil_matrix((N,N), dtype='int8')


#adj_block = sparse.csr_matrix((N,N), dtype='int8')


for indices in interconnections.values():

    # it might happen that a node to interconnect appears only on one layer
    if len(indices) == 1:
        continue
        
    # only the portion below the diagonal of the inter adj matrix is used in multinetX
    # use it to make the perform better (if not, run at all!)
    
    indices.sort(reverse=True)
    
    pos = 0
    
    # if we have more than 2 layers the we want to process them all
    while (pos+2) <= len(indices):
        
        print('{} Updating matrix position:{},{}'.format(pos, indices[pos], indices[pos+1]))
        
        adj_block[indices[pos],indices[pos+1]] = 1
        
        pos += 1
        
print('Done up updateing one half of the matrix...')
    
#adj_block += adj_block.T # looks like this operation is not doable at all...

#print(adj_block.data.nbytes + adj_block.indices.nbytes + adj_block.indptr.nbytes )

print('The matrix is all set...')

0 Updating matrix position:106041,52939
1 Updating matrix position:52939,0
0 Updating matrix position:106042,52940
1 Updating matrix position:52940,1
0 Updating matrix position:106043,52941
1 Updating matrix position:52941,2
0 Updating matrix position:106044,52942
1 Updating matrix position:52942,3
0 Updating matrix position:106045,52943
1 Updating matrix position:52943,4
0 Updating matrix position:106046,52944
1 Updating matrix position:52944,5
0 Updating matrix position:106047,52945
1 Updating matrix position:52945,6
0 Updating matrix position:106048,52946
1 Updating matrix position:52946,7
0 Updating matrix position:106049,52947
1 Updating matrix position:52947,8
0 Updating matrix position:106050,52948
1 Updating matrix position:52948,9
0 Updating matrix position:106051,52949
1 Updating matrix position:52949,10
0 Updating matrix position:106052,52950
1 Updating matrix position:52950,11
0 Updating matrix position:106053,52951
1 Updating matrix position:52951,12
0 Updating matrix posi

0 Updating matrix position:107110,54008
1 Updating matrix position:54008,1068
0 Updating matrix position:107111,54009
1 Updating matrix position:54009,1069
0 Updating matrix position:107112,54010
1 Updating matrix position:54010,1070
0 Updating matrix position:107113,54011
1 Updating matrix position:54011,1071
0 Updating matrix position:107114,54012
1 Updating matrix position:54012,1072
0 Updating matrix position:107115,54013
1 Updating matrix position:54013,1073
0 Updating matrix position:107116,54014
1 Updating matrix position:54014,1074
0 Updating matrix position:107117,54015
1 Updating matrix position:54015,1075
0 Updating matrix position:107118,54016
1 Updating matrix position:54016,1076
0 Updating matrix position:107119,54017
1 Updating matrix position:54017,1077
0 Updating matrix position:107120,54018
1 Updating matrix position:54018,1078
0 Updating matrix position:107121,54019
1 Updating matrix position:54019,1079
0 Updating matrix position:107122,54020
1 Updating matrix positi

0 Updating matrix position:107686,54584
1 Updating matrix position:54584,1644
0 Updating matrix position:107687,54585
1 Updating matrix position:54585,1645
0 Updating matrix position:107688,54586
1 Updating matrix position:54586,1646
0 Updating matrix position:107689,54587
1 Updating matrix position:54587,1647
0 Updating matrix position:107690,54588
1 Updating matrix position:54588,1648
0 Updating matrix position:107691,54589
1 Updating matrix position:54589,1649
0 Updating matrix position:107692,54590
1 Updating matrix position:54590,1650
0 Updating matrix position:107693,54591
1 Updating matrix position:54591,1651
0 Updating matrix position:107694,54592
1 Updating matrix position:54592,1652
0 Updating matrix position:107695,54593
1 Updating matrix position:54593,1653
0 Updating matrix position:107696,54594
1 Updating matrix position:54594,1654
0 Updating matrix position:107697,54595
1 Updating matrix position:54595,1655
0 Updating matrix position:107699,54597
1 Updating matrix positi

1 Updating matrix position:54834,1893
0 Updating matrix position:107937,54835
1 Updating matrix position:54835,1894
0 Updating matrix position:107938,54836
1 Updating matrix position:54836,1895
0 Updating matrix position:107939,54837
1 Updating matrix position:54837,1896
0 Updating matrix position:107940,54838
1 Updating matrix position:54838,1897
0 Updating matrix position:107941,54839
1 Updating matrix position:54839,1898
0 Updating matrix position:107942,54840
1 Updating matrix position:54840,1899
0 Updating matrix position:107943,54841
1 Updating matrix position:54841,1900
0 Updating matrix position:107944,54842
1 Updating matrix position:54842,1901
0 Updating matrix position:107945,54843
1 Updating matrix position:54843,1902
0 Updating matrix position:107946,54844
1 Updating matrix position:54844,1903
0 Updating matrix position:107947,54845
1 Updating matrix position:54845,1904
0 Updating matrix position:107948,54846
1 Updating matrix position:54846,1905
0 Updating matrix position

1 Updating matrix position:55334,2393
0 Updating matrix position:108437,55335
1 Updating matrix position:55335,2394
0 Updating matrix position:108438,55336
1 Updating matrix position:55336,2395
0 Updating matrix position:108439,55337
1 Updating matrix position:55337,2396
0 Updating matrix position:108440,55338
1 Updating matrix position:55338,2397
0 Updating matrix position:108441,55339
1 Updating matrix position:55339,2398
0 Updating matrix position:108442,55340
1 Updating matrix position:55340,2399
0 Updating matrix position:108443,55341
1 Updating matrix position:55341,2400
0 Updating matrix position:108444,55342
1 Updating matrix position:55342,2401
0 Updating matrix position:108445,55343
1 Updating matrix position:55343,2402
0 Updating matrix position:108446,55344
1 Updating matrix position:55344,2403
0 Updating matrix position:108447,55345
1 Updating matrix position:55345,2404
0 Updating matrix position:108448,55346
1 Updating matrix position:55346,2405
0 Updating matrix position

...

0 Updating matrix position:154704,101602
1 Updating matrix position:101602,48631
0 Updating matrix position:154705,101603
1 Updating matrix position:101603,48632
0 Updating matrix position:154706,101604
1 Updating matrix position:101604,48633
0 Updating matrix position:154707,101605
1 Updating matrix position:101605,48634
0 Updating matrix position:154708,101606
1 Updating matrix position:101606,48635
0 Updating matrix position:154709,101607
1 Updating matrix position:101607,48636
0 Updating matrix position:154710,101608
1 Updating matrix position:101608,48637
0 Updating matrix position:154711,101609
1 Updating matrix position:101609,48638
0 Updating matrix position:154712,101610
1 Updating matrix position:101610,48639
0 Updating matrix position:154713,101611
1 Updating matrix position:101611,48640
0 Updating matrix position:154714,101612
1 Updating matrix position:101612,48641
0 Updating matrix position:154715,101613
1 Updating matrix position:101613,48642
0 Updating matrix position:1

1 Updating matrix position:102601,49630
0 Updating matrix position:155704,102602
1 Updating matrix position:102602,49631
0 Updating matrix position:155705,102603
1 Updating matrix position:102603,49632
0 Updating matrix position:155706,102604
1 Updating matrix position:102604,49633
0 Updating matrix position:155707,102605
1 Updating matrix position:102605,49634
0 Updating matrix position:155708,102606
1 Updating matrix position:102606,49635
0 Updating matrix position:155709,102607
1 Updating matrix position:102607,49636
0 Updating matrix position:155710,102608
1 Updating matrix position:102608,49637
0 Updating matrix position:155711,102609
1 Updating matrix position:102609,49638
0 Updating matrix position:155712,102610
1 Updating matrix position:102610,49639
0 Updating matrix position:155713,102611
1 Updating matrix position:102611,49640
0 Updating matrix position:155714,102612
1 Updating matrix position:102612,49641
0 Updating matrix position:155715,102613
1 Updating matrix position:1

0 Updating matrix position:156706,103604
1 Updating matrix position:103604,50631
0 Updating matrix position:156707,103605
1 Updating matrix position:103605,50632
0 Updating matrix position:156708,103606
1 Updating matrix position:103606,50633
0 Updating matrix position:156709,103607
1 Updating matrix position:103607,50634
0 Updating matrix position:156710,103608
1 Updating matrix position:103608,50635
0 Updating matrix position:156711,103609
1 Updating matrix position:103609,50636
0 Updating matrix position:156712,103610
1 Updating matrix position:103610,50637
0 Updating matrix position:156713,103611
1 Updating matrix position:103611,50638
0 Updating matrix position:156714,103612
1 Updating matrix position:103612,50639
0 Updating matrix position:156715,103613
1 Updating matrix position:103613,50640
0 Updating matrix position:156716,103614
1 Updating matrix position:103614,50641
0 Updating matrix position:156717,103615
1 Updating matrix position:103615,50642
0 Updating matrix position:1

0 Updating matrix position:157708,104606
1 Updating matrix position:104606,51631
0 Updating matrix position:157709,104607
1 Updating matrix position:104607,51632
0 Updating matrix position:157710,104608
1 Updating matrix position:104608,51633
0 Updating matrix position:157711,104609
1 Updating matrix position:104609,51634
0 Updating matrix position:157712,104610
1 Updating matrix position:104610,51635
0 Updating matrix position:157713,104611
1 Updating matrix position:104611,51636
0 Updating matrix position:157714,104612
1 Updating matrix position:104612,51637
0 Updating matrix position:157715,104613
1 Updating matrix position:104613,51638
0 Updating matrix position:157716,104614
1 Updating matrix position:104614,51639
0 Updating matrix position:157717,104615
1 Updating matrix position:104615,51640
0 Updating matrix position:157718,104616
1 Updating matrix position:104616,51641
0 Updating matrix position:157719,104617
1 Updating matrix position:104617,51642
0 Updating matrix position:1

0 Updating matrix position:158709,105607
1 Updating matrix position:105607,52631
0 Updating matrix position:158710,105608
1 Updating matrix position:105608,52632
0 Updating matrix position:158711,105609
1 Updating matrix position:105609,52633
0 Updating matrix position:158712,105610
1 Updating matrix position:105610,52634
0 Updating matrix position:158713,105611
1 Updating matrix position:105611,52635
0 Updating matrix position:158714,105612
1 Updating matrix position:105612,52636
0 Updating matrix position:158715,105613
1 Updating matrix position:105613,52637
0 Updating matrix position:158716,105614
1 Updating matrix position:105614,52638
0 Updating matrix position:158717,105615
1 Updating matrix position:105615,52639
0 Updating matrix position:158718,105616
1 Updating matrix position:105616,52640
0 Updating matrix position:158719,105617
1 Updating matrix position:105617,52641
0 Updating matrix position:158720,105618
1 Updating matrix position:105618,52642
0 Updating matrix position:1

In [25]:
for l in layers:
    print(get_node_count_stats(l))

(52939, 52761, 178)
(53102, 52781, 321)
(53084, 52798, 286)


In [26]:
adj_block
#print(adj_block)
#print(type(adj_block2))

<159125x159125 sparse matrix of type '<class 'numpy.int8'>'
	with 105542 stored elements in List of Lists format>

In [27]:
# just for debugging purposes!
#layers[0].nodes(data=True)

In [28]:
# just for debugging purposes!
#layers[1].nodes(data=True)

In [29]:
mg = mx.MultilayerGraph(list_of_layers=layers, inter_adjacency_matrix=adj_block)
# next two lines gives an error!
#mg.add_layer(g_loc)
#mg.add_layer(g_disc)

# mg.layers_interconnect(inter_adjacency_matrix=adj_block)
# this should also be possible thrugh a named parameter to the constructor:

# mx.MultilayerGraph(list_of_layers=[g1,g2,g3], inter_adjacency_matrix=adj_block)

In [ ]:
# just to be aple to plot someting below...

mg.set_edges_weights(intra_layer_edges_weight=1,
                     inter_layer_edges_weight=1)

# this below gives an error on the weights when plotting!
#mg.set_edges_weights(inter_layer_edges_weight=3)

#mg.set_intra_edges_weights(layer=0,weight=1)
#mg.set_intra_edges_weights(layer=1,weight=2)

In [ ]:
# this block from here:
# https://github.com/nkoub/multinetx#plot-the-adjacency-matrix-and-the-multiplex-networks-2

fig = plt.figure(figsize=(15,5))
ax1 = fig.add_subplot(121)
ax1.imshow(mx.adjacency_matrix(mg,weight='weight').todense(),origin='upper',interpolation='nearest',cmap=plt.cm.jet_r)
ax1.set_title('supra adjacency matrix')

ax2 = fig.add_subplot(122)
ax2.axis('off')
ax2.set_title('regular interconnected network')
pos = mx.get_position(mg,mx.fruchterman_reingold_layout(mg.get_layer(0)),layer_vertical_shift=1.4,layer_horizontal_shift=0.0,proj_angle=7)
mx.draw_networkx(mg,pos=pos,ax=ax2,node_size=50,with_labels=False,edge_color=[mg[a][b]['weight'] for a,b in mg.edges()],edge_cmap=plt.cm.jet_r)
plt.show()

In [30]:
type(mx.adjacency_matrix(mg))

scipy.sparse.csr.csr_matrix

Thre is also this way..

In [ ]:
adj_mat = nx.to_numpy_matrix(mg)
type(adj_mat)
# propably not as memory efficient as the other sparse formats

In [ ]:
with np.printoptions(threshold=np.inf):
    print(mx.adjacency_matrix(mg).toarray())
    
# there is a slightly updated approach to this in the np quickstart tutorial

In [31]:
# one option, if stm was of type scipy.sparse.lil.lil_matrix, would be to normalize it like this.
#stm = stm / stm.sum() #wouldn't need to depend of the machine learning librari for that one.

stm = normalize(mx.adjacency_matrix(mg), norm='l1', axis=0) #default parameters: copy=True
stm

<159125x159125 sparse matrix of type '<class 'numpy.float64'>'
	with 548044 stored elements in Compressed Sparse Column format>

In [32]:
type(stm)

scipy.sparse.csc.csc_matrix

In [ ]:
#with np.printoptions(threshold=np.inf):
#    print(stm)

# the following is acc. to current quickstart tutorial
np.set_printoptions(threshold=sys.maxsize)
print(stm)

In [ ]:
def get_R_matrix(matrix, label):
    
    nrow = matrix.shape[0]
    ncol = matrix.shape[1]
    
    print('{}<-matrix(0, nrow = {}, ncol = {})'.format(label,nrow,ncol)) #SA <- matrix(0, nrow = 15, ncol = 15)

    for row in range(nrow):
        for col in range(ncol):
            if matrix[row,col] > 0:
                print('{}[{},{}]<-1'.format(label, row+1, col+1))

In [ ]:
get_R_matrix(mx.adjacency_matrix(mg), 'SA')

In [ ]:
mg.nodes(data=True)

In [ ]:
pm, pm_indexes = persoal_matrix_from_defaulters('defaultersSmall.txt', mg)

In [ ]:
# type(pm)
pm

In [ ]:
get_R_matrix(pm, 'PersonalMatrix')

In [ ]:
alpha = 0.85

In [ ]:
stm2 = alpha * stm + (1 - alpha)/pm.sum() * pm

In [ ]:
print(stm2)

In [ ]:
eigenvalues, eigenvectors = linalg.eig(stm2.toarray()) #the most general one, not sure of others are better

In [ ]:
np.all(np.isreal(eigenvalues)) # we might get imaginary eigenvalues right!

In [ ]:
real_eigenvalues = [np.real(x) for x in eigenvalues] # if only real numbers let's work with those only

In [ ]:
leading_eigenvalue = np.real(max(eigenvalues))
leading_eigenvalue

In [ ]:
lev_index = real_eigenvalues.index(leading_eigenvalue) #is it always so that the leading eigenvalue comes first in the array of those?
lev_index

In [ ]:
leading_eigenvector = eigenvectors[:, lev_index]
leading_eigenvector

In [ ]:
 leading_eigenvector.sum()

In [ ]:
leading_eigenvector_norm = leading_eigenvector / leading_eigenvector.sum()

In [ ]:
leading_eigenvector_norm

In [ ]:
leading_eigenvector_norm.sum()

In [ ]:
type(leading_eigenvector)

In [ ]:
personalization = {}
for i_list in pm_indexes.values():
    for i in i_list:
        personalization[i] = 1

In [ ]:
personalization

In [ ]:
p_rank_power = nx.pagerank(mg, personalization=personalization)
p_rank_power

In [ ]:
s = 0
for num in p_rank_power.values():
    s += num
s